In [1]:
import torch
import torchvision
from torch.autograd import Variable
import torch.nn as nn
import torch.nn.functional as F

from torch.utils.data import Dataset, DataLoader
from torchvision import transforms, utils
import torch.optim as optim
import torchvision.transforms as standard_transforms

import numpy as np
import glob

from data_loader import Rescale
from data_loader import RescaleT
from data_loader import RandomCrop
from data_loader import CenterCrop
from data_loader import ToTensor
from data_loader import ToTensorLab
from data_loader import SalObjDataset

from model import BASNet

import pytorch_ssim
import pytorch_iou


In [2]:
bce_loss = nn.BCELoss(size_average=True)
ssim_loss = pytorch_ssim.SSIM(window_size=11,size_average=True)
iou_loss = pytorch_iou.IOU(size_average=True)

def bce_ssim_loss(pred,target):

	bce_out = bce_loss(pred,target)
	ssim_out = 1 - ssim_loss(pred,target)
	iou_out = iou_loss(pred,target)

	loss = bce_out + ssim_out + iou_out

	return loss

def muti_bce_loss_fusion(d0, d1, d2, d3, d4, d5, d6, d7, labels_v):

	loss0 = bce_ssim_loss(d0,labels_v)
	loss1 = bce_ssim_loss(d1,labels_v)
	loss2 = bce_ssim_loss(d2,labels_v)
	loss3 = bce_ssim_loss(d3,labels_v)
	loss4 = bce_ssim_loss(d4,labels_v)
	loss5 = bce_ssim_loss(d5,labels_v)
	loss6 = bce_ssim_loss(d6,labels_v)
	loss7 = bce_ssim_loss(d7,labels_v)
	#ssim0 = 1 - ssim_loss(d0,labels_v)

	# iou0 = iou_loss(d0,labels_v)
	#loss = torch.pow(torch.mean(torch.abs(labels_v-d0)),2)*(5.0*loss0 + loss1 + loss2 + loss3 + loss4 + loss5) #+ 5.0*lossa
	loss = loss0 + loss1 + loss2 + loss3 + loss4 + loss5 + loss6 + loss7#+ 5.0*lossa
	print("l0: %3f, l1: %3f, l2: %3f, l3: %3f, l4: %3f, l5: %3f, l6: %3f\n"%(loss0.data[0],loss1.data[0],loss2.data[0],loss3.data[0],loss4.data[0],loss5.data[0],loss6.data[0]))
	# print("BCE: l1:%3f, l2:%3f, l3:%3f, l4:%3f, l5:%3f, la:%3f, all:%3f\n"%(loss1.data[0],loss2.data[0],loss3.data[0],loss4.data[0],loss5.data[0],lossa.data[0],loss.data[0]))

	return loss0, loss

C:\Users\yangz\miniconda3-2\envs\p36_3\lib\site-packages\torch\nn\functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


In [3]:
tra_image_dir = 'C:/Users/yangz/Desktop/FireProjectBatchDownloadNew/PerimeterTrainingDataRescaledV4Filtered/TrainingRF-V4-'
lbl_image_dir = 'C:/Users/yangz/Desktop/FireProjectBatchDownloadNew/PerimeterLabelsRescaledV3Filtered/LabelRF-V3-'

model_dir = 'C:/Users/yangz/Desktop/FireProject/BASNet/saved_models/basnet_bsi-Copy1/'

epoch_num = 100
batch_size_train = 2
batch_size_val = 1
train_num = 0
val_num = 0

tra_img_name_list = glob.glob(tra_image_dir + '*.jpg')
tra_lbl_name_list = glob.glob(lbl_image_dir + '*.png')

print("---")
print("train images: ", len(tra_img_name_list))
print("train labels: ", len(tra_lbl_name_list))
print("---")

train_num = len(tra_img_name_list)

salobj_dataset = SalObjDataset(
    img_name_list=tra_img_name_list,
    lbl_name_list=tra_lbl_name_list,
    transform=transforms.Compose([
        RescaleT(256),
        RandomCrop(224),
        ToTensorLab(flag=0)]))
salobj_dataloader = DataLoader(salobj_dataset, batch_size=batch_size_train, shuffle=True, num_workers=1)

---
train images:  792
train labels:  792
---


In [4]:
net = BASNet(3, 1)
if torch.cuda.is_available():
    print ("Using CUDA")
    net.cuda()


Using CUDA


In [5]:
print("---define optimizer...")
optimizer = optim.Adam(net.parameters(), lr=0.0001, betas=(0.9, 0.999), eps=1e-08, weight_decay=0)

---define optimizer...


In [6]:
net.load_state_dict(torch.load(model_dir+"basnet_bsi_itr_37680_train_6.026760_tar_0.654454.pth"))

In [7]:
print("---start training...")
ite_num = 37680
running_loss = 0.0
running_tar_loss = 0.0
ite_num4val = 0

for epoch in range(0, epoch_num):
    print ("Starting epoch " + str(epoch+1))
    net.train()
    print ("Epoch " + str(epoch+1) + " loading complete")

    for i, data in enumerate(salobj_dataloader):
        ite_num = ite_num + 1
        ite_num4val = ite_num4val + 1

        inputs, labels = data['image'], data['label']

        inputs = inputs.type(torch.FloatTensor)
        labels = labels.type(torch.FloatTensor)

        # wrap them in Variable
        if torch.cuda.is_available():
            inputs_v, labels_v = Variable(inputs.cuda(), requires_grad=False), Variable(labels.cuda(),
                                                                                        requires_grad=False)
        else:
            inputs_v, labels_v = Variable(inputs, requires_grad=False), Variable(labels, requires_grad=False)

        # y zero the parameter gradients
        optimizer.zero_grad()

        # forward + backward + optimize
        d0, d1, d2, d3, d4, d5, d6, d7 = net(inputs_v)
        loss2, loss = muti_bce_loss_fusion(d0, d1, d2, d3, d4, d5, d6, d7, labels_v)

        loss.backward()
        optimizer.step()

        # # print statistics
        running_loss += loss.data.item()
        running_tar_loss += loss2.data.item()

        # del temporary outputs and loss
        del d0, d1, d2, d3, d4, d5, d6, d7, loss2, loss

        print("[epoch: %3d/%3d, batch: %5d/%5d, ite: %d] train loss: %3f, tar: %3f " % (
        epoch + 1, epoch_num, (i + 1) * batch_size_train, train_num, ite_num, running_loss / ite_num4val, running_tar_loss / ite_num4val))

        if ite_num % 2000 == 0:  # save model every 2000 iterations

            torch.save(net.state_dict(), model_dir + "basnet_bsi_itr_%d_train_%3f_tar_%3f.pth" % (ite_num, running_loss / ite_num4val, running_tar_loss / ite_num4val))
            running_loss = 0.0
            running_tar_loss = 0.0
            net.train()  # resume train
            ite_num4val = 0
            
print('-------------Congratulations! Training Done!!!-------------')


---start training...
Starting epoch 1
Epoch 1 loading complete


C:\Users\yangz\miniconda3-2\envs\p36_3\lib\site-packages\torch\nn\modules\upsampling.py:122: UserWarning: nn.Upsampling is deprecated. Use nn.functional.interpolate instead.
  warnings.warn("nn.Upsampling is deprecated. Use nn.functional.interpolate instead.")
C:\Users\yangz\miniconda3-2\envs\p36_3\lib\site-packages\torch\nn\functional.py:1961: UserWarning: Default upsampling behavior when mode=bilinear is changed to align_corners=False since 0.4.0. Please specify align_corners=True if the old behavior is desired. See the documentation of nn.Upsample for details.
  "See the documentation of nn.Upsample for details.".format(mode))
C:\Users\yangz\miniconda3-2\envs\p36_3\lib\site-packages\torch\nn\functional.py:1006: UserWarning: nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.
  warnings.warn("nn.functional.sigmoid is deprecated. Use torch.sigmoid instead.")
C:\Users\yangz\miniconda3-2\envs\p36_3\lib\site-packages\ipykernel_launcher.py:30: UserWarning: invalid index of a 0

l0: 0.367253, l1: 0.377961, l2: 0.380019, l3: 0.379838, l4: 0.376151, l5: 0.425060, l6: 0.634960

[epoch:   1/100, batch:     2/  792, ite: 37681] train loss: 3.584586, tar: 0.367253 
l0: 0.758641, l1: 0.758841, l2: 0.757465, l3: 0.761288, l4: 0.776782, l5: 0.811884, l6: 1.141542

[epoch:   1/100, batch:     4/  792, ite: 37682] train loss: 5.212924, tar: 0.562947 
l0: 0.473289, l1: 0.473604, l2: 0.472447, l3: 0.486701, l4: 0.536152, l5: 0.647107, l6: 0.754759

[epoch:   1/100, batch:     6/  792, ite: 37683] train loss: 5.048249, tar: 0.533061 
l0: 0.629045, l1: 0.640108, l2: 0.632993, l3: 0.608896, l4: 0.576087, l5: 0.642872, l6: 0.687504

[epoch:   1/100, batch:     8/  792, ite: 37684] train loss: 5.097287, tar: 0.557057 
l0: 0.871136, l1: 0.871136, l2: 0.866297, l3: 0.859257, l4: 0.922133, l5: 0.880153, l6: 0.829255

[epoch:   1/100, batch:    10/  792, ite: 37685] train loss: 5.478712, tar: 0.619873 
l0: 0.585558, l1: 0.586165, l2: 0.583674, l3: 0.588250, l4: 0.585267, l5: 0.6679

[epoch:   1/100, batch:    90/  792, ite: 37725] train loss: 5.797239, tar: 0.631550 
l0: 0.677483, l1: 0.683855, l2: 0.684382, l3: 0.687657, l4: 0.701528, l5: 0.810135, l6: 0.967836

[epoch:   1/100, batch:    92/  792, ite: 37726] train loss: 5.806103, tar: 0.632549 
l0: 1.007214, l1: 1.001238, l2: 1.000159, l3: 1.021104, l4: 1.041667, l5: 1.024222, l6: 1.173312

[epoch:   1/100, batch:    94/  792, ite: 37727] train loss: 5.863662, tar: 0.640521 
l0: 0.946786, l1: 0.942809, l2: 0.950620, l3: 0.967885, l4: 1.013265, l5: 0.975959, l6: 1.678691

[epoch:   1/100, batch:    96/  792, ite: 37728] train loss: 5.934289, tar: 0.646901 
l0: 0.434200, l1: 0.435142, l2: 0.432904, l3: 0.434518, l4: 0.440164, l5: 0.522613, l6: 0.743333

[epoch:   1/100, batch:    98/  792, ite: 37729] train loss: 5.897840, tar: 0.642560 
l0: 0.567639, l1: 0.572970, l2: 0.582245, l3: 0.592165, l4: 0.675996, l5: 0.830135, l6: 0.981245

[epoch:   1/100, batch:   100/  792, ite: 37730] train loss: 5.897398, tar: 0.64

[epoch:   1/100, batch:   180/  792, ite: 37770] train loss: 5.816148, tar: 0.630615 
l0: 0.836859, l1: 0.833678, l2: 0.829198, l3: 0.836995, l4: 0.879282, l5: 0.999840, l6: 1.072367

[epoch:   1/100, batch:   182/  792, ite: 37771] train loss: 5.832632, tar: 0.632881 
l0: 0.619388, l1: 0.618659, l2: 0.617527, l3: 0.615045, l4: 0.638254, l5: 0.765310, l6: 0.921692

[epoch:   1/100, batch:   184/  792, ite: 37772] train loss: 5.832685, tar: 0.632734 
l0: 0.998807, l1: 1.003852, l2: 1.002972, l3: 1.004835, l4: 1.008461, l5: 1.100683, l6: 1.426455

[epoch:   1/100, batch:   186/  792, ite: 37773] train loss: 5.866330, tar: 0.636671 
l0: 0.822903, l1: 0.825570, l2: 0.828991, l3: 0.832494, l4: 0.821455, l5: 0.940885, l6: 1.191861

[epoch:   1/100, batch:   188/  792, ite: 37774] train loss: 5.882906, tar: 0.638652 
l0: 0.660094, l1: 0.668755, l2: 0.672010, l3: 0.676300, l4: 0.705167, l5: 0.777700, l6: 1.055940

[epoch:   1/100, batch:   190/  792, ite: 37775] train loss: 5.887274, tar: 0.63

...

[epoch:  83/100, batch:   142/  792, ite: 70223] train loss: 4.093524, tar: 0.413510 
l0: 0.824657, l1: 0.834231, l2: 0.830423, l3: 0.832918, l4: 0.859579, l5: 0.915166, l6: 0.999889

[epoch:  83/100, batch:   144/  792, ite: 70224] train loss: 4.107282, tar: 0.415345 
l0: 0.194502, l1: 0.198330, l2: 0.195645, l3: 0.193476, l4: 0.253296, l5: 0.412479, l6: 0.662440

[epoch:  83/100, batch:   146/  792, ite: 70225] train loss: 4.101750, tar: 0.414364 
l0: 0.670599, l1: 0.668305, l2: 0.668912, l3: 0.670386, l4: 0.709891, l5: 0.742274, l6: 0.892775

[epoch:  83/100, batch:   148/  792, ite: 70226] train loss: 4.109920, tar: 0.415498 
l0: 0.304655, l1: 0.305112, l2: 0.307860, l3: 0.310821, l4: 0.347626, l5: 0.455830, l6: 0.605181

[epoch:  83/100, batch:   150/  792, ite: 70227] train loss: 4.106430, tar: 0.415009 
l0: 0.389787, l1: 0.396970, l2: 0.400233, l3: 0.410713, l4: 0.454009, l5: 0.673491, l6: 0.825487

[epoch:  83/100, batch:   152/  792, ite: 70228] train loss: 4.107867, tar: 0.41

[epoch:  83/100, batch:   232/  792, ite: 70268] train loss: 4.124544, tar: 0.416596 
l0: 0.543344, l1: 0.544739, l2: 0.547200, l3: 0.552638, l4: 0.586775, l5: 0.612180, l6: 0.793398

[epoch:  83/100, batch:   234/  792, ite: 70269] train loss: 4.127712, tar: 0.417067 
l0: 0.392740, l1: 0.395855, l2: 0.394807, l3: 0.402701, l4: 0.405402, l5: 0.492200, l6: 0.751492

[epoch:  83/100, batch:   236/  792, ite: 70270] train loss: 4.127274, tar: 0.416977 
l0: 0.519348, l1: 0.521983, l2: 0.522557, l3: 0.527858, l4: 0.551183, l5: 0.724288, l6: 0.883394

[epoch:  83/100, batch:   238/  792, ite: 70271] train loss: 4.131297, tar: 0.417355 
l0: 0.401872, l1: 0.405226, l2: 0.407615, l3: 0.423649, l4: 0.452606, l5: 0.559829, l6: 0.639219

[epoch:  83/100, batch:   240/  792, ite: 70272] train loss: 4.130603, tar: 0.417298 
l0: 0.542180, l1: 0.559205, l2: 0.558582, l3: 0.563299, l4: 0.567555, l5: 0.617736, l6: 0.665161

[epoch:  83/100, batch:   242/  792, ite: 70273] train loss: 4.133197, tar: 0.41

[epoch:  83/100, batch:   322/  792, ite: 70313] train loss: 4.138738, tar: 0.418200 
l0: 0.643266, l1: 0.649426, l2: 0.647716, l3: 0.633634, l4: 0.633729, l5: 0.706775, l6: 0.844448

[epoch:  83/100, batch:   324/  792, ite: 70314] train loss: 4.143782, tar: 0.418916 
l0: 0.279484, l1: 0.294493, l2: 0.299267, l3: 0.305379, l4: 0.354315, l5: 0.443435, l6: 0.654873

[epoch:  83/100, batch:   326/  792, ite: 70315] train loss: 4.141285, tar: 0.418474 
l0: 0.314175, l1: 0.314073, l2: 0.317019, l3: 0.328038, l4: 0.356245, l5: 0.497217, l6: 0.582103

[epoch:  83/100, batch:   328/  792, ite: 70316] train loss: 4.138777, tar: 0.418144 
l0: 0.511136, l1: 0.520633, l2: 0.521560, l3: 0.520107, l4: 0.529944, l5: 0.575518, l6: 0.650693

[epoch:  83/100, batch:   330/  792, ite: 70317] train loss: 4.140021, tar: 0.418437 
l0: 0.755155, l1: 0.756461, l2: 0.762475, l3: 0.756222, l4: 0.763763, l5: 0.812049, l6: 0.954450

[epoch:  83/100, batch:   332/  792, ite: 70318] train loss: 4.148090, tar: 0.41

[epoch:  83/100, batch:   412/  792, ite: 70358] train loss: 4.109449, tar: 0.414495 
l0: 0.681393, l1: 0.675330, l2: 0.685193, l3: 0.709125, l4: 0.759261, l5: 0.832546, l6: 1.247115

[epoch:  83/100, batch:   414/  792, ite: 70359] train loss: 4.117292, tar: 0.415238 
l0: 0.333863, l1: 0.338008, l2: 0.340816, l3: 0.331716, l4: 0.349418, l5: 0.455210, l6: 0.633740

[epoch:  83/100, batch:   416/  792, ite: 70360] train loss: 4.115536, tar: 0.415012 
l0: 0.625593, l1: 0.632823, l2: 0.631651, l3: 0.631683, l4: 0.661118, l5: 0.732697, l6: 1.046134

[epoch:  83/100, batch:   418/  792, ite: 70361] train loss: 4.120723, tar: 0.415595 
l0: 0.356384, l1: 0.359398, l2: 0.358598, l3: 0.351610, l4: 0.381177, l5: 0.477565, l6: 0.654785

[epoch:  83/100, batch:   420/  792, ite: 70362] train loss: 4.119603, tar: 0.415432 
l0: 0.348571, l1: 0.352094, l2: 0.351852, l3: 0.359599, l4: 0.383234, l5: 0.463814, l6: 0.625288

[epoch:  83/100, batch:   422/  792, ite: 70363] train loss: 4.118092, tar: 0.41

KeyboardInterrupt: 

In [ ]:
#21:23 - 21:30

In [8]:
torch.save(net.state_dict(), model_dir + "basnet_bsi_itr_%d_train_%3f_tar_%3f.pth" % (ite_num, running_loss / ite_num4val, running_tar_loss / ite_num4val))